# Zusammenfassung der Analysen vom Hackathon für die Webside

- womöglich zur Darstellung auf der Webside


In [14]:
import numpy as np
import pandas as pd
import altair as alt

## Daten aufbereitung

Dump der Datenbank vom 25.03.2023. Die verschiedene Tabellen der Datenbank werden einzeln eingelesen. Zusätzlich werden alle direkt zu einem Tweet zugehörige Information in ein Datenobjekt gesammelt. Die Informationen zu den GIS-Daten zu den einzelnen Polizeistadtion ("police_stations") sind noch unvollständig und müssen gegebenfalls nocheinmal überprüft werden.



In [6]:
tweets_meta = pd.read_csv("data/tweets.csv")
tweets_time = pd.read_csv("data/tweets-1679742620302.csv")
tweets_text = pd.read_csv("data/tweets-1679742698645.csv")
tweets_user = pd.read_csv("data/tweets-1679742702794.csv"
                         ).rename(columns = {"username":"handle", # rename columns
                                             "handle": "username"})
tweets_user = tweets_user.assign(handle = tweets_user['handle'].str.lower()) # convert handles to lower case
tweets_combined = pd.merge(tweets_time, # merge the two tweet related data frames
                           tweets_text, 
                           how = 'inner', 
                           on = 'tweet_id'
                          ).drop(['id'], # drop unascessary id column (redundant to index)
                                 axis = 1)
tweets_combined = tweets_combined.assign(measured_at = pd.to_datetime(tweets_combined['measured_at']), # change date to date format
                                         created_at  = pd.to_datetime(tweets_combined['created_at']))
police_stations = pd.read_csv("data/polizei_accounts_geo.csv", sep = "\t"  # addiditional on police stations
                             ).rename(columns = {"Polizei Account": "handle"})
tweets_combined.head()

tweet_id         measured_at  like_count  reply_count  \
0  1496955054712045581 2022-02-28 22:42:26          13            0   
1  1496957213516214277 2022-02-28 22:42:26           2            0   
2  1496963501201539073 2022-02-28 22:42:26          -1           -1   
3  1496963771054825472 2022-02-28 23:42:27         142            7   
4  1496965696907104258 2022-02-28 23:42:27           0            0   

   retweet_count  quote_count  is_deleted  \
0              2            0           0   
1              0            0           0   
2             -1           -1           1   
3              8            3           0   
4             11            0           0   

                                          tweet_text          created_at  \
0  Auch wir schließen uns dem Apell an! \n\n#Ukra... 2022-02-24 21:07:51   
1  @BWeltenbummler Sehr schwer zu sagen. Die Evak... 2022-02-24 21:16:26   
2  Halten Sie durch – die Evakuierung ist fast ab... 2022-02-24 21:41:25   
3  Halten Sie durch – die Evakuierung ist fast ab... 2022-02-24 21:42:29   
4  RT @drkberlin_iuk: 🚨 In enger Abstimmung mit d... 2022-02-24 21:50:09   

              user_id  
0  773438463068766208  
1          2397974054  
2          2398002414  
3          2398002414  
4          2398002414

### Adjazenzmatrix mentions
 
Information, welche nicht direkt enthalten ist: welche Accounts werden erwähnt. Ist nur im Tweet mit @handle gekennzeichnet.

In [53]:
# TODO

0    Auch wir schließen uns dem Apell an! \n\n#Ukra...
1    @BWeltenbummler Sehr schwer zu sagen. Die Evak...
2    Halten Sie durch – die Evakuierung ist fast ab...
3    Halten Sie durch – die Evakuierung ist fast ab...
4    RT @drkberlin_iuk: 🚨 In enger Abstimmung mit d...
Name: tweet_text, dtype: object

## Metadaten 

Welche Daten bilden die Grundlage?

In [7]:
tweets_meta["entity_type"].value_counts()
# tweets_meta[tweets_meta['entity_type'] == "mention"]

hashtag    157145
url         88322
mention     36815
Name: entity_type, dtype: int64

Insgesamt haben wir 84794 einzigartige Tweets:

In [8]:
tweets_combined["tweet_id"].value_counts().shape[0] # Anzahl an Tweets

84794

In [9]:
print("Die Tweets wurden vom ", tweets_combined['created_at'].min().date(), "bis zum:", tweets_combined['created_at'].max().date(), "gesammelt.", "Also genau insgesamt:", (tweets_combined['created_at'].max() - tweets_combined['created_at'].min()).days, "Tage.")
# tweets_combined[tweets_combined['created_at'] == tweets_combined['created_at'].max()] # Tweets vom letzten Tag

Die Tweets wurden vom  2022-02-24 bis zum: 2023-03-16 gesammelt. Also genau insgesamt: 384 Tage.


Welche Polizei Accounts haben am meisten getweetet?

In [43]:
tweets_agg = tweets_combined.merge(tweets_user,
                                   on = "user_id"
                                  ).groupby(by = ["user_id", "handle", "username"]
                              )["user_id"].aggregate(['count']
                                                    ).merge(police_stations, 
                                                            on = "handle",
                                                            how = "left"
                                                           ).sort_values(['count'], 
                                                                         ascending=False)
tweets_agg.shape
activy_police_vis = tweets_agg[0:50]
activy_police_vis.headd()

handle  count             Name      Typ           Bundesland  \
11     polizei_ffm   2993              NaN      NaN                  NaN   
3   polizei_nrw_do   2860   Polizei NRW DO  Polizei  Nordrhein-Westfalen   
0   polizeisachsen   2700  Polizei Sachsen  Polizei              Sachsen   
91       polizeibb   2310              NaN      NaN                  NaN   
61  polizeihamburg   2093  Polizei Hamburg  Polizei              Hamburg   

       Stadt         LAT        LONG  
11       NaN         NaN         NaN  
3   Dortmund  51.5142273   7.4652789  
0    Dresden  51.0493286  13.7381437  
91       NaN         NaN         NaN  
61   Hamburg   53.550341   10.000654

Visualisierung aktivste Polizeistadtionen:

In [47]:
barchart = alt.Chart(activy_police_vis[0:15]).mark_bar().encode(
    x = 'count:Q',
    y = alt.Y('handle:N', sort = '-x'),
)
barchart 

alt.Chart(...)

Welche Tweets ziehen besonders viel Aufmerksamkeit auf sich?

In [90]:
tweets_attention = tweets_combined.merge(tweets_user,
                                            on = "user_id",
                                            how = "left"
                                            ).merge(police_stations,
                                                    on = "handle",
                                                    how = "left")
pd.options.display.max_colwidth = 100
tweets_attention.sort_values('like_count', ascending = False).reset_index()['tweet_text']



0        Die Gewalt, die unsere Kolleginnen &amp; Kollegen in der Silvesternacht erleben mussten, ist une...
1        WICHTIGE Info:\nÜber das Internet wird derzeit ein Video verbreitet, in dem von einem Überfall a...
2        Die Experten gehen derzeit davon aus, dass es sich um ein absichtliches "Fake-Video" handelt, da...
3        Auf unserem #A45 in #lichterfelde) befindet sich gerade diese Fundhündin. Sie wurde am Hindenbur...
4        @nexta_tv Wir haben das Video gesichert und leiten den Sachverhalt an die zuständigen Kolleginne...
                                                        ...                                                 
84789    #Polizeimeldungen #Tagesticker\n \nAnhalt-Bitterfeld\nhttps://t.co/tNLEzztL1o\n \nDessau-Roßlau\...
84790    Am Mittwoch erhielten wir mehrere Anrufe über einen auffälligen Pkw-Fahrer (Reifen quietschen un...
84791                         @Jonas5Luisa Kleiner Pro-Tipp von uns: Einfach mal auf den link klicken! ;)*cl
84792    Vermissten